In [0]:
from pyspark.sql import SparkSession,Window
import pandas as pd
from pyspark.sql.functions import isnan, when, count, col,udf,max
from matplotlib import pyplot as plt 
import datetime
import re
from pyspark.sql.types import IntegerType
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.classification import RandomForestClassifier,GBTClassifier
from pyspark.ml.feature import StandardScaler
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
import time
from pyspark.ml.evaluation import BinaryClassificationEvaluator
import seaborn as sns
import numpy as np

In [0]:
spark = SparkSession.builder \
    .master("local") \
    .appName("my_sparkify") \
    .getOrCreate()

In [0]:
storage_account_name = "nypbigdatastorage"
storage_account_access_key = "W86xe/oS/fZujFMoku3wahZMNzipVRnTWPvkphyl23Csmn4xOad+0ay9ZPcfzYgWucMaT8qzHs+fGiRmOZ2PFQ=="
file_checkin = "wasbs://nypbigdatacontainer@nypbigdatastorage.blob.core.windows.net/checkin.json"
file_biz = "wasbs://nypbigdatacontainer@nypbigdatastorage.blob.core.windows.net/biz.json"
#file_location = "wasbs://nypbigdatacontainer@nypbigdatastorage.blob.core.windows.net/user.json"
#file_location = "wasbs://nypbigdatacontainer@nypbigdatastorage.blob.core.windows.net/review.json"
# file_location = "wasbs://nypbigdatacontainer@nypbigdatastorage.blob.core.windows.net/tip.json"
file_type = "json"
spark.conf.set(
  "fs.azure.account.key."+storage_account_name+".blob.core.windows.net",
  storage_account_access_key)

In [0]:
checkin_df_spark = spark.read.format(file_type).option("inferSchema", "true").load(file_checkin)
biz_df_spark = spark.read.format(file_type).option("inferSchema", "true").load(file_biz)

In [0]:
display(checkin_df_spark)

business_id date --1UhMGODdWsrMastO9DZw 2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016-10-15 02:45:18, 2016-11-18 01:54:50, 2017-04-20 18:39:06, 2017-05-03 17:58:02, 2019-03-19 22:04:48 --6MefnULPED_I942VcFNA 2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012-04-15 01:07:50, 2012-05-06 23:08:42, 2012-06-08 22:43:12, 2012-08-06 23:20:52, 2012-08-19 18:30:44, 2013-01-27 23:49:51, 2013-03-01 01:22:29, 2013-03-23 21:53:47, 2013-03-24 01:11:51, 2013-05-20 00:12:25, 2013-06-29 22:50:57, 2013-07-01 15:58:04, 2013-07-01 22:35:42, 2013-07-28 21:46:49, 2013-08-02 22:06:03, 2013-08-11 18:42:03, 2013-08-23 01:29:56, 2013-09-17 17:40:36, 2013-09-20 23:36:30, 2013-09-24 23:50:18, 2013-10-12 23:11:13, 2013-11-24 18:40:15, 2013-12-12 02:52:54, 2013-12-26 17:33:17, 2013-12-30 00:27:37, 2014-03-28 23:38:23, 2014-04-25 22:48:11, 2014-04-28 22:56:07, 2014-05-03 01:02:47, 2014-05-19 17:08:37, 2014-06-16 00:04:51, 2014-06-22 17:21:27, 2014-07-04 19:13:34, 2014-07-11 15:46:29, 2014-07-25 20:55:48, 2014-08-23 22:27:42, 2014-08-31 01:43:10, 2014-09-06 16:29:55, 2014-09-13 23:34:42, 2014-10-11 23:20:09, 2014-11-19 19:05:56, 2014-11-30 23:27:15, 2015-01-04 01:06:47, 2015-01-04 01:08:08, 2015-01-11 00:16:13, 2015-01-17 23:42:09, 2015-01-17 23:46:42, 2015-01-26 00:05:15, 2015-02-18 17:21:01, 2015-03-22 22:26:09, 2015-03-28 22:47:50, 2015-04-03 21:49:35, 2015-04-05 18:52:21, 2015-04-11 22:59:11, 2015-04-12 22:52:29, 2015-04-24 00:02:22, 2015-05-09 21:45:34, 2015-05-16 22:53:44, 2015-06-07 17:54:51, 2015-07-01 16:24:54, 2015-07-10 22:13:09, 2015-07-11 22:16:37, 2015-07-18 00:27:00, 2015-08-29 23:51:50, 2015-09-07 22:57:51, 2015-09-27 23:54:33, 2015-10-11 22:03:40, 2015-10-12 15:08:23, 2015-10-23 01:34:21, 2015-10-25 00:36:12, 2015-11-09 18:55:17, 2015-11-15 00:01:47, 2015-12-16 19:59:00, 2015-12-27 01:00:59, 2016-01-23 19:05:37, 2016-01-30 23:54:10, 2016-02-07 03:19:01, 2016-02-13 17:49:41, 2016-02-16 00:16:10, 2016-03-27 21:14:50, 2016-04-02 16:29:16, 2016-04-02 17:17:50, 2016-04-16 22:27:48, 2016-04-27 23:54:21, 2016-05-07 21:52:13, 2016-05-21 22:14:00, 2016-06-04 23:06:32, 2016-06-11 22:23:48, 2016-07-01 02:59:31, 2016-07-02 23:01:47, 2016-07-06 22:27:12, 2016-07-08 00:49:30, 2016-07-16 23:53:17, 2016-07-26 17:15:19, 2016-08-01 22:46:32, 2016-08-02 00:14:10, 2016-08-18 03:19:16, 2016-08-20 12:47:15, 2016-08-21 12:24:31, 2016-09-15 20:31:53, 2016-10-03 01:04:15, 2016-10-03 01:04:25, 2016-11-26 00:48:51, 2016-12-24 17:56:29, 2016-12-31 18:29:26, 2017-01-09 01:07:12, 2017-01-15 03:53:00, 2017-01-15 17:30:16, 2017-01-28 00:44:48, 2017-02-10 20:18:01, 2017-02-18 23:13:18, 2017-02-19 00:30:24, 2017-02-20 02:04:48, 2017-04-16 22:46:55, 2017-04-27 04:38:34, 2017-05-13 22:51:49, 2017-05-19 23:03:19, 2017-05-31 22:46:11, 2017-05-31 22:46:33, 2017-07-28 23:38:19, 2017-08-13 23:42:59, 2017-08-17 23:27:33, 2017-09-03 17:30:25, 2017-09-03 22:59:25, 2017-09-16 21:12:41, 2017-09-18 00:36:34, 2017-09-28 23:28:02, 2017-10-01 13:02:01, 2017-10-08 00:00:05, 2017-10-08 15:07:36, 2017-10-09 00:44:22, 2017-10-15 22:31:47, 2017-10-17 23:31:26, 2017-10-17 23:32:10, 2017-11-04 22:48:12, 2017-11-10 20:50:25, 2017-12-17 23:02:32, 2017-12-21 00:55:13, 2017-12-29 01:53:12, 2017-12-29 01:53:52, 2018-01-26 00:47:30, 2018-03-30 16:49:10, 2018-04-07 16:27:21, 2018-04-24 23:45:19, 2018-05-05 18:27:12, 2018-05-05 22:27:18, 2018-05-14 23:47:27, 2018-05-20 23:49:45, 2018-05-25 16:39:21, 2018-06-04 21:40:47, 2018-06-04 21:40:58, 2018-06-12 22:27:30, 2018-06-20 22:53:27, 2018-07-05 16:15:18, 2018-07-08 18:40:13, 2018-07-08 20:41:46, 2018-07-18 20:58:49, 2018-07-24 23:35:44, 2018-08-09 00:08:56, 2018-08-20 22:29:00, 2018-08-31 17:47:54, 2018-09-13 23:08:09, 2018-09-15 22:16:51, 2018-10-21 18:09:02, 2018-10-21 22:58:14, 2018-11-24 00:37:46, 2018-12-17 01:22:50, 2018-12-29 17:15:48, 2019-01-01 22:41:14, 2019-01-06 23:16:27, 2019-02-09 19:09:55, 2019-02-10 00:04:52, 2019-03-02 23:45:36, 2019-04-20 22:27:13, 2019-05-05 00:23:49, 2019-05-05 18:28:36, 2019-05-05 22:04:14, 2019-05-14 23:35:44, 2019-05-18 

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import *
checkin=checkin_df_spark.withColumn('Numofcheckin',F.size(F.split(F.col('date'),",")))
display(checkin)

business_id date Numofcheckin --1UhMGODdWsrMastO9DZw 2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016-10-15 02:45:18, 2016-11-18 01:54:50, 2017-04-20 18:39:06, 2017-05-03 17:58:02, 2019-03-19 22:04:48 7 --6MefnULPED_I942VcFNA 2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012-04-15 01:07:50, 2012-05-06 23:08:42, 2012-06-08 22:43:12, 2012-08-06 23:20:52, 2012-08-19 18:30:44, 2013-01-27 23:49:51, 2013-03-01 01:22:29, 2013-03-23 21:53:47, 2013-03-24 01:11:51, 2013-05-20 00:12:25, 2013-06-29 22:50:57, 2013-07-01 15:58:04, 2013-07-01 22:35:42, 2013-07-28 21:46:49, 2013-08-02 22:06:03, 2013-08-11 18:42:03, 2013-08-23 01:29:56, 2013-09-17 17:40:36, 2013-09-20 23:36:30, 2013-09-24 23:50:18, 2013-10-12 23:11:13, 2013-11-24 18:40:15, 2013-12-12 02:52:54, 2013-12-26 17:33:17, 2013-12-30 00:27:37, 2014-03-28 23:38:23, 2014-04-25 22:48:11, 2014-04-28 22:56:07, 2014-05-03 01:02:47, 2014-05-19 17:08:37, 2014-06-16 00:04:51, 2014-06-22 17:21:27, 2014-07-04 19:13:34, 2014-07-11 15:46:29, 2014-07-25 20:55:48, 2014-08-23 22:27:42, 2014-08-31 01:43:10, 2014-09-06 16:29:55, 2014-09-13 23:34:42, 2014-10-11 23:20:09, 2014-11-19 19:05:56, 2014-11-30 23:27:15, 2015-01-04 01:06:47, 2015-01-04 01:08:08, 2015-01-11 00:16:13, 2015-01-17 23:42:09, 2015-01-17 23:46:42, 2015-01-26 00:05:15, 2015-02-18 17:21:01, 2015-03-22 22:26:09, 2015-03-28 22:47:50, 2015-04-03 21:49:35, 2015-04-05 18:52:21, 2015-04-11 22:59:11, 2015-04-12 22:52:29, 2015-04-24 00:02:22, 2015-05-09 21:45:34, 2015-05-16 22:53:44, 2015-06-07 17:54:51, 2015-07-01 16:24:54, 2015-07-10 22:13:09, 2015-07-11 22:16:37, 2015-07-18 00:27:00, 2015-08-29 23:51:50, 2015-09-07 22:57:51, 2015-09-27 23:54:33, 2015-10-11 22:03:40, 2015-10-12 15:08:23, 2015-10-23 01:34:21, 2015-10-25 00:36:12, 2015-11-09 18:55:17, 2015-11-15 00:01:47, 2015-12-16 19:59:00, 2015-12-27 01:00:59, 2016-01-23 19:05:37, 2016-01-30 23:54:10, 2016-02-07 03:19:01, 2016-02-13 17:49:41, 2016-02-16 00:16:10, 2016-03-27 21:14:50, 2016-04-02 16:29:16, 2016-04-02 17:17:50, 2016-04-16 22:27:48, 2016-04-27 23:54:21, 2016-05-07 21:52:13, 2016-05-21 22:14:00, 2016-06-04 23:06:32, 2016-06-11 22:23:48, 2016-07-01 02:59:31, 2016-07-02 23:01:47, 2016-07-06 22:27:12, 2016-07-08 00:49:30, 2016-07-16 23:53:17, 2016-07-26 17:15:19, 2016-08-01 22:46:32, 2016-08-02 00:14:10, 2016-08-18 03:19:16, 2016-08-20 12:47:15, 2016-08-21 12:24:31, 2016-09-15 20:31:53, 2016-10-03 01:04:15, 2016-10-03 01:04:25, 2016-11-26 00:48:51, 2016-12-24 17:56:29, 2016-12-31 18:29:26, 2017-01-09 01:07:12, 2017-01-15 03:53:00, 2017-01-15 17:30:16, 2017-01-28 00:44:48, 2017-02-10 20:18:01, 2017-02-18 23:13:18, 2017-02-19 00:30:24, 2017-02-20 02:04:48, 2017-04-16 22:46:55, 2017-04-27 04:38:34, 2017-05-13 22:51:49, 2017-05-19 23:03:19, 2017-05-31 22:46:11, 2017-05-31 22:46:33, 2017-07-28 23:38:19, 2017-08-13 23:42:59, 2017-08-17 23:27:33, 2017-09-03 17:30:25, 2017-09-03 22:59:25, 2017-09-16 21:12:41, 2017-09-18 00:36:34, 2017-09-28 23:28:02, 2017-10-01 13:02:01, 2017-10-08 00:00:05, 2017-10-08 15:07:36, 2017-10-09 00:44:22, 2017-10-15 22:31:47, 2017-10-17 23:31:26, 2017-10-17 23:32:10, 2017-11-04 22:48:12, 2017-11-10 20:50:25, 2017-12-17 23:02:32, 2017-12-21 00:55:13, 2017-12-29 01:53:12, 2017-12-29 01:53:52, 2018-01-26 00:47:30, 2018-03-30 16:49:10, 2018-04-07 16:27:21, 2018-04-24 23:45:19, 2018-05-05 18:27:12, 2018-05-05 22:27:18, 2018-05-14 23:47:27, 2018-05-20 23:49:45, 2018-05-25 16:39:21, 2018-06-04 21:40:47, 2018-06-04 21:40:58, 2018-06-12 22:27:30, 2018-06-20 22:53:27, 2018-07-05 16:15:18, 2018-07-08 18:40:13, 2018-07-08 20:41:46, 2018-07-18 20:58:49, 2018-07-24 23:35:44, 2018-08-09 00:08:56, 2018-08-20 22:29:00, 2018-08-31 17:47:54, 2018-09-13 23:08:09, 2018-09-15 22:16:51, 2018-10-21 18:09:02, 2018-10-21 22:58:14, 2018-11-24 00:37:46, 2018-12-17 01:22:50, 2018-12-29 17:15:48, 2019-01-01 22:41:14, 2019-01-06 23:16:27, 2019-02-09 19:09:55, 2019-02-10 00:04:52, 2019-03-02 23:45:36, 2019-04-20 22:27:13, 2019-05-05 00:23:49, 2019-05-05 18:28:36, 2019-05-05 22:04:14, 2019-05-14 23:35:

In [0]:
checkin.createOrReplaceTempView("checkin")

In [0]:
%sql
create or replace temporary view checkin_1 as select *,explode(split(to_date(date),","))Dates from checkin

In [0]:
%sql
select * from checkin_1

business_id date Numofcheckin Dates --1UhMGODdWsrMastO9DZw 2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016-10-15 02:45:18, 2016-11-18 01:54:50, 2017-04-20 18:39:06, 2017-05-03 17:58:02, 2019-03-19 22:04:48 7 2016-04-26 --6MefnULPED_I942VcFNA 2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012-04-15 01:07:50, 2012-05-06 23:08:42, 2012-06-08 22:43:12, 2012-08-06 23:20:52, 2012-08-19 18:30:44, 2013-01-27 23:49:51, 2013-03-01 01:22:29, 2013-03-23 21:53:47, 2013-03-24 01:11:51, 2013-05-20 00:12:25, 2013-06-29 22:50:57, 2013-07-01 15:58:04, 2013-07-01 22:35:42, 2013-07-28 21:46:49, 2013-08-02 22:06:03, 2013-08-11 18:42:03, 2013-08-23 01:29:56, 2013-09-17 17:40:36, 2013-09-20 23:36:30, 2013-09-24 23:50:18, 2013-10-12 23:11:13, 2013-11-24 18:40:15, 2013-12-12 02:52:54, 2013-12-26 17:33:17, 2013-12-30 00:27:37, 2014-03-28 23:38:23, 2014-04-25 22:48:11, 2014-04-28 22:56:07, 2014-05-03 01:02:47, 2014-05-19 17:08:37, 2014-06-16 00:04:51, 2014-06-22 17:21:27, 2014-07-04 19:13:34, 2014-07-11 15:46:29, 2014-07-25 20:55:48, 2014-08-23 22:27:42, 2014-08-31 01:43:10, 2014-09-06 16:29:55, 2014-09-13 23:34:42, 2014-10-11 23:20:09, 2014-11-19 19:05:56, 2014-11-30 23:27:15, 2015-01-04 01:06:47, 2015-01-04 01:08:08, 2015-01-11 00:16:13, 2015-01-17 23:42:09, 2015-01-17 23:46:42, 2015-01-26 00:05:15, 2015-02-18 17:21:01, 2015-03-22 22:26:09, 2015-03-28 22:47:50, 2015-04-03 21:49:35, 2015-04-05 18:52:21, 2015-04-11 22:59:11, 2015-04-12 22:52:29, 2015-04-24 00:02:22, 2015-05-09 21:45:34, 2015-05-16 22:53:44, 2015-06-07 17:54:51, 2015-07-01 16:24:54, 2015-07-10 22:13:09, 2015-07-11 22:16:37, 2015-07-18 00:27:00, 2015-08-29 23:51:50, 2015-09-07 22:57:51, 2015-09-27 23:54:33, 2015-10-11 22:03:40, 2015-10-12 15:08:23, 2015-10-23 01:34:21, 2015-10-25 00:36:12, 2015-11-09 18:55:17, 2015-11-15 00:01:47, 2015-12-16 19:59:00, 2015-12-27 01:00:59, 2016-01-23 19:05:37, 2016-01-30 23:54:10, 2016-02-07 03:19:01, 2016-02-13 17:49:41, 2016-02-16 00:16:10, 2016-03-27 21:14:50, 2016-04-02 16:29:16, 2016-04-02 17:17:50, 2016-04-16 22:27:48, 2016-04-27 23:54:21, 2016-05-07 21:52:13, 2016-05-21 22:14:00, 2016-06-04 23:06:32, 2016-06-11 22:23:48, 2016-07-01 02:59:31, 2016-07-02 23:01:47, 2016-07-06 22:27:12, 2016-07-08 00:49:30, 2016-07-16 23:53:17, 2016-07-26 17:15:19, 2016-08-01 22:46:32, 2016-08-02 00:14:10, 2016-08-18 03:19:16, 2016-08-20 12:47:15, 2016-08-21 12:24:31, 2016-09-15 20:31:53, 2016-10-03 01:04:15, 2016-10-03 01:04:25, 2016-11-26 00:48:51, 2016-12-24 17:56:29, 2016-12-31 18:29:26, 2017-01-09 01:07:12, 2017-01-15 03:53:00, 2017-01-15 17:30:16, 2017-01-28 00:44:48, 2017-02-10 20:18:01, 2017-02-18 23:13:18, 2017-02-19 00:30:24, 2017-02-20 02:04:48, 2017-04-16 22:46:55, 2017-04-27 04:38:34, 2017-05-13 22:51:49, 2017-05-19 23:03:19, 2017-05-31 22:46:11, 2017-05-31 22:46:33, 2017-07-28 23:38:19, 2017-08-13 23:42:59, 2017-08-17 23:27:33, 2017-09-03 17:30:25, 2017-09-03 22:59:25, 2017-09-16 21:12:41, 2017-09-18 00:36:34, 2017-09-28 23:28:02, 2017-10-01 13:02:01, 2017-10-08 00:00:05, 2017-10-08 15:07:36, 2017-10-09 00:44:22, 2017-10-15 22:31:47, 2017-10-17 23:31:26, 2017-10-17 23:32:10, 2017-11-04 22:48:12, 2017-11-10 20:50:25, 2017-12-17 23:02:32, 2017-12-21 00:55:13, 2017-12-29 01:53:12, 2017-12-29 01:53:52, 2018-01-26 00:47:30, 2018-03-30 16:49:10, 2018-04-07 16:27:21, 2018-04-24 23:45:19, 2018-05-05 18:27:12, 2018-05-05 22:27:18, 2018-05-14 23:47:27, 2018-05-20 23:49:45, 2018-05-25 16:39:21, 2018-06-04 21:40:47, 2018-06-04 21:40:58, 2018-06-12 22:27:30, 2018-06-20 22:53:27, 2018-07-05 16:15:18, 2018-07-08 18:40:13, 2018-07-08 20:41:46, 2018-07-18 20:58:49, 2018-07-24 23:35:44, 2018-08-09 00:08:56, 2018-08-20 22:29:00, 2018-08-31 17:47:54, 2018-09-13 23:08:09, 2018-09-15 22:16:51, 2018-10-21 18:09:02, 2018-10-21 22:58:14, 2018-11-24 00:37:46, 2018-12-17 01:22:50, 2018-12-29 17:15:48, 2019-01-01 22:41:14, 2019-01-06 23:16:27, 2019-02-09 19:09:55, 2019-02-10 00:04:52, 2019-03-02 23:45:36, 2019-04-20 22:27:13, 2019-05-05 00:23:49, 2019-05-05 18:28:36, 2019-05-05 22:04:14, 

In [0]:
checkin_data=sqlContext.sql("select * from checkin_1")
display(checkin_data)

business_id date Numofcheckin Dates --1UhMGODdWsrMastO9DZw 2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016-10-15 02:45:18, 2016-11-18 01:54:50, 2017-04-20 18:39:06, 2017-05-03 17:58:02, 2019-03-19 22:04:48 7 2016-04-26 --6MefnULPED_I942VcFNA 2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012-04-15 01:07:50, 2012-05-06 23:08:42, 2012-06-08 22:43:12, 2012-08-06 23:20:52, 2012-08-19 18:30:44, 2013-01-27 23:49:51, 2013-03-01 01:22:29, 2013-03-23 21:53:47, 2013-03-24 01:11:51, 2013-05-20 00:12:25, 2013-06-29 22:50:57, 2013-07-01 15:58:04, 2013-07-01 22:35:42, 2013-07-28 21:46:49, 2013-08-02 22:06:03, 2013-08-11 18:42:03, 2013-08-23 01:29:56, 2013-09-17 17:40:36, 2013-09-20 23:36:30, 2013-09-24 23:50:18, 2013-10-12 23:11:13, 2013-11-24 18:40:15, 2013-12-12 02:52:54, 2013-12-26 17:33:17, 2013-12-30 00:27:37, 2014-03-28 23:38:23, 2014-04-25 22:48:11, 2014-04-28 22:56:07, 2014-05-03 01:02:47, 2014-05-19 17:08:37, 2014-06-16 00:04:51, 2014-06-22 17:21:27, 2014-07-04 19:13:34, 2014-07-11 15:46:29, 2014-07-25 20:55:48, 2014-08-23 22:27:42, 2014-08-31 01:43:10, 2014-09-06 16:29:55, 2014-09-13 23:34:42, 2014-10-11 23:20:09, 2014-11-19 19:05:56, 2014-11-30 23:27:15, 2015-01-04 01:06:47, 2015-01-04 01:08:08, 2015-01-11 00:16:13, 2015-01-17 23:42:09, 2015-01-17 23:46:42, 2015-01-26 00:05:15, 2015-02-18 17:21:01, 2015-03-22 22:26:09, 2015-03-28 22:47:50, 2015-04-03 21:49:35, 2015-04-05 18:52:21, 2015-04-11 22:59:11, 2015-04-12 22:52:29, 2015-04-24 00:02:22, 2015-05-09 21:45:34, 2015-05-16 22:53:44, 2015-06-07 17:54:51, 2015-07-01 16:24:54, 2015-07-10 22:13:09, 2015-07-11 22:16:37, 2015-07-18 00:27:00, 2015-08-29 23:51:50, 2015-09-07 22:57:51, 2015-09-27 23:54:33, 2015-10-11 22:03:40, 2015-10-12 15:08:23, 2015-10-23 01:34:21, 2015-10-25 00:36:12, 2015-11-09 18:55:17, 2015-11-15 00:01:47, 2015-12-16 19:59:00, 2015-12-27 01:00:59, 2016-01-23 19:05:37, 2016-01-30 23:54:10, 2016-02-07 03:19:01, 2016-02-13 17:49:41, 2016-02-16 00:16:10, 2016-03-27 21:14:50, 2016-04-02 16:29:16, 2016-04-02 17:17:50, 2016-04-16 22:27:48, 2016-04-27 23:54:21, 2016-05-07 21:52:13, 2016-05-21 22:14:00, 2016-06-04 23:06:32, 2016-06-11 22:23:48, 2016-07-01 02:59:31, 2016-07-02 23:01:47, 2016-07-06 22:27:12, 2016-07-08 00:49:30, 2016-07-16 23:53:17, 2016-07-26 17:15:19, 2016-08-01 22:46:32, 2016-08-02 00:14:10, 2016-08-18 03:19:16, 2016-08-20 12:47:15, 2016-08-21 12:24:31, 2016-09-15 20:31:53, 2016-10-03 01:04:15, 2016-10-03 01:04:25, 2016-11-26 00:48:51, 2016-12-24 17:56:29, 2016-12-31 18:29:26, 2017-01-09 01:07:12, 2017-01-15 03:53:00, 2017-01-15 17:30:16, 2017-01-28 00:44:48, 2017-02-10 20:18:01, 2017-02-18 23:13:18, 2017-02-19 00:30:24, 2017-02-20 02:04:48, 2017-04-16 22:46:55, 2017-04-27 04:38:34, 2017-05-13 22:51:49, 2017-05-19 23:03:19, 2017-05-31 22:46:11, 2017-05-31 22:46:33, 2017-07-28 23:38:19, 2017-08-13 23:42:59, 2017-08-17 23:27:33, 2017-09-03 17:30:25, 2017-09-03 22:59:25, 2017-09-16 21:12:41, 2017-09-18 00:36:34, 2017-09-28 23:28:02, 2017-10-01 13:02:01, 2017-10-08 00:00:05, 2017-10-08 15:07:36, 2017-10-09 00:44:22, 2017-10-15 22:31:47, 2017-10-17 23:31:26, 2017-10-17 23:32:10, 2017-11-04 22:48:12, 2017-11-10 20:50:25, 2017-12-17 23:02:32, 2017-12-21 00:55:13, 2017-12-29 01:53:12, 2017-12-29 01:53:52, 2018-01-26 00:47:30, 2018-03-30 16:49:10, 2018-04-07 16:27:21, 2018-04-24 23:45:19, 2018-05-05 18:27:12, 2018-05-05 22:27:18, 2018-05-14 23:47:27, 2018-05-20 23:49:45, 2018-05-25 16:39:21, 2018-06-04 21:40:47, 2018-06-04 21:40:58, 2018-06-12 22:27:30, 2018-06-20 22:53:27, 2018-07-05 16:15:18, 2018-07-08 18:40:13, 2018-07-08 20:41:46, 2018-07-18 20:58:49, 2018-07-24 23:35:44, 2018-08-09 00:08:56, 2018-08-20 22:29:00, 2018-08-31 17:47:54, 2018-09-13 23:08:09, 2018-09-15 22:16:51, 2018-10-21 18:09:02, 2018-10-21 22:58:14, 2018-11-24 00:37:46, 2018-12-17 01:22:50, 2018-12-29 17:15:48, 2019-01-01 22:41:14, 2019-01-06 23:16:27, 2019-02-09 19:09:55, 2019-02-10 00:04:52, 2019-03-02 23:45:36, 2019-04-20 22:27:13, 2019-05-05 00:23:49, 2019-05-05 18:28:36, 2019-05-05 22:04:14, 

In [0]:
column_to_drop=['date']
new_checkin_data=checkin_data.drop(*column_to_drop)
display(new_checkin_data)

business_id Numofcheckin Dates --1UhMGODdWsrMastO9DZw 7 2016-04-26 --6MefnULPED_I942VcFNA 189 2011-06-04 --7zmmkVg-IMGaXbuVd0SQ 193 2014-12-29 --8LPVSo5i0Oo61X01sV9A 1 2016-07-08 --9QQLMTbFzLJ_oT-ON3Xw 38 2010-06-26 --9e1ONYQuAa-CB_Rrw7Tw 2942 2010-02-08 --DaPTJW3-tB1vP-PfdTEg 97 2012-06-03 --DdmeR16TRb3LsjG0ejrQ 30 2012-11-02 --EF5N7P70J_UYBTPypYlA 3 2018-05-25 --EX4rRznJrltyn-34Jz1w 17 2010-02-26 --FBCX-N37CMYDfs790Bnw 552 2010-05-31 --FLdgM0GNpXVMn74ppCGw 16 2012-10-23 --FnvijzY20d1nk9H7fk9w 9 2019-09-19 --GM_ORV2cYS-h38DSaCLw 38 2011-09-11 --I7YYLada0tSLkORTHb5Q 116 2014-11-07 --KCl2FvVQpvjzmZSPyviA 107 2011-07-29 --KQsXc-clkO7oHRqGzSzg 778 2010-05-02 --Ni3oJ4VOqfOEu7Sj2Vzg 1 2019-06-07 --Rsj71PBe31h5YljVseKA 309 2011-12-15 --S62v0QgkqQaVUhFnNHrw 68 2010-12-25 --SrzpvFLwP_YFwB_Cetow 150 2011-02-10 --TcDRzRIxhvHM4DSgEuMA 9 2012-03-05 --U98MNlDym2cLn36BBPgQ 3 2011-10-05 --WsruI0IGEoeRmkErU5Gg 2 2018-08-04 --Y1Adl1YUWfYIRSd8vkmA 4 2011-05-03 --Y7NhBKzLTbNliMUX_wfg 4 2015-03-26 --YPwqIlRJrhHkJcjY3eiA 2 2016-06-18 --ab39IjZR_xUf81WyTyHg 69 2010-11-23 --cZ6Hhc9F7VkKXxHMVZSQ 753 2010-04-24 --cgVkbWTiga3OYTkymKqA 3 2010-08-10 --cjBEbXMI2obtaRHNSFrA 149 2015-04-09 --e8PjCNhEz32pprnPhCwQ 1 2015-04-02 --g-a85VwrdZJNf0R95GcQ 26 2013-11-28 --i1tTcggBi4cPkd-h5hDg 93 2010-03-16 --irMpXK9y_xLlXPvPAQvw 17 2011-05-05 --kinfHwmtdjz03g8B8z8Q 3 2014-08-27 --lZAZSwpP_axKoL4lR9dQ 1 2015-09-13 --phjqoPSPa8sLmUVNby9w 48 2011-01-20 --q6datkI-f0EoVheXNEeQ 4 2014-01-28 --q7kSBRb0vWC8lSkXFByA 107 2010-09-26 --qvQS4MigHPykD2GV0-zw 1 2019-04-11 --ttCFj_csKJhxnaMRNuiw 20 2012-01-20 --ujyvoQlwVoBgMYtADiLA 285 2010-10-30 --wIGbLEhlpl_UeAIyDmZQ 2 2015-06-06 --z7PM8AGaJP0aBmGMY7RA 27 2012-09-06 -000aQFeK6tqVLndf7xORg 1 2018-10-17 -01XupAWZEXbdNbxNg5mEg 333 2010-03-23 -03HVYxkeYWaafEpNJo1SA 11 2015-11-29 -050d_XIor1NpCuWkbIVaQ 1484 2010-01-23 -05uZNVbb8DhFweTEOoDVg 23 2011-09-17 -06-Fdi30wJx-JA8P7CAng 90 2011-02-25 -092wE7j5HZOogMLAh40zA 78 2010-07-28 -0CCHBui57tZ_1y_14X-5Q 12 2017-09-23 -0CTrPQNiSyClxhdO4HSDQ 56 2010-10-13 -0DET7VdEQOJVJ_v6klEug 296 2017-05-01 -0DwB6Swi349EKfbBAOF7A 44 2011-08-03 -0FA-Qdi3SPYIoJz9UQw-A 3 2018-09-29 -0Fendn2TmhDJ-1s6gPi5g 14 2011-09-30 -0GU6ghA7z4-xotUZfXl1w 57 2011-07-20 -0Hj1hb_XW6ybWq2M7QhGA 6 2011-04-23 -0K4W5p3wbQe_vDoB5jMgQ 28 2017-08-10 -0KMvRFwDWdVBeTpT11iHw 3 2012-07-13 -0KSt9tXv6C015vmAcSIcg 23 2016-08-03 -0KqNhmK40DTzwUPM_Ik9g 144 2010-10-10 -0LPtgJC31FWMrMv317p0Q 3 2013-04-13 -0M3o2uWBnQZwd3hmfEwuw 3 2016-09-10 -0NhdsDJsdarxyDPR523ZQ 24 2010-05-10 -0NrB58jqKqJfuUCDupcsw 187 2014-06-12 -0QtTRrAMn6DKLZNef3Ojg 3 2016-07-23 -0RRiWDtfnS16AKCtfvBZg 7 2017-05-19 -0RU0vASJOV383dYA8VZgA 25 2018-04-06 -0RkJ_uIduNLWQrphbADRw 181 2018-08-30 -0Sgh0QlUKVsWosCWJzGqQ 44 2010-12-05 -0Soj75v-XoRcf2ERr8Bmg 1 2019-06-05 -0T0jfPnuBRdpNTXpOQZcA 20 2012-12-28 -0VImVWDeqewaA3th8fzIg 3 2011-01-17 -0WegMt6Cy966qlDKhu6jA 387 2013-04-04 -0XFoI1UKfuRKwyAl85zAQ 15 2012-01-08 -0YY5yQ3ufLB6EoPBsHGig 2 2012-11-01 -0ZO00Vm2ADchytlEkoXmg 60 2013-07-10 -0ZumLlFjMh4ZW1z2nXGug 5 2011-09-24 -0aIra_B6iALlfqAriBSYA 72 2015-06-27 -0aOudcaAyac0VJbMX-L1g 4 2015-03-16 -0b86isaXMY0v4g-V8GZ9Q 2 2013-10-22 -0d-BfFSU0bwLcnMaGRxYw 5 2014-08-07 -0dWjxaPKrXAn8urSnkSLA 118 2010-07-08 -0gEYa7iHAshDcMvJ0Vuag 42 2018-02-06 -0jz6c3C6i7RG7Ag22K-Pg 3 2015-05-02 -0lbeUxS9QDBtIS5KtPKZw 1 2018-08-16 -0mgn9dRi95otXd_h61LdA 57 2011-06-24 -0mm8pqBSIOYZQHeo8XnkA 59 2013-07-30 -0nEqS3_A_nnUut4DrEPEg 7 2015-11-10 -0oNlErLlU7PQa-TpespdA 11 2011-06-19 -0qht1roIqleKiQkBLDkbw 1344 2010-04-08 -0qqsy04kcYdXH3DOciaZw 117 2011-08-21 -0t6o9LXMVQ3aV8CHhRTnA 425 2016-04-20 -0tgMGl7D9B10YjSN2ujLA 826 2010-01-29 -0uEqc2vw1xXtuI_r1xTNg 9 2012-09-27 -0y3MZU2oYP8r1ruDP1bfQ 5 2015-04-11 -113IAvSQ4Nn_Jk7OrrPkg 1 2011-03-18 -11PbySWhJQtK6USx4IP2A 109 2017-03-04 -17RjDnOY9c7IsCcYUjx5Q 30 2012-01-26 -1BPe8UjF2_l3nVk-DFUjA 3 2015-12-03 -1CI4H3DLkI-NdWLbIae6g 9 2013-11-21 -1E2CQu_38mkghvmZgCCRw 1 2019-04-04 -1G5n-Pnu3I7gjh7-_VRxw 4 2015-03-02 -1HW4ALuB331RgjwHOA0Nw 20 2012-02-03 -1Jq9x77Es6Ce1EJM4WhwQ 2

In [0]:
year=new_checkin_data.withColumn('Year',F.year(F.to_date(col("Dates"))))
month=year.withColumn('Month',F.month(F.to_date(col('Dates'))))
dayofweek=month.withColumn("DayofWeek", date_format(col("Dates"), "E"))
display(dayofweek)

business_id Numofcheckin Dates Year Month DayofWeek --1UhMGODdWsrMastO9DZw 7 2016-04-26 2016 4 Tue --6MefnULPED_I942VcFNA 189 2011-06-04 2011 6 Sat --7zmmkVg-IMGaXbuVd0SQ 193 2014-12-29 2014 12 Mon --8LPVSo5i0Oo61X01sV9A 1 2016-07-08 2016 7 Fri --9QQLMTbFzLJ_oT-ON3Xw 38 2010-06-26 2010 6 Sat --9e1ONYQuAa-CB_Rrw7Tw 2942 2010-02-08 2010 2 Mon --DaPTJW3-tB1vP-PfdTEg 97 2012-06-03 2012 6 Sun --DdmeR16TRb3LsjG0ejrQ 30 2012-11-02 2012 11 Fri --EF5N7P70J_UYBTPypYlA 3 2018-05-25 2018 5 Fri --EX4rRznJrltyn-34Jz1w 17 2010-02-26 2010 2 Fri --FBCX-N37CMYDfs790Bnw 552 2010-05-31 2010 5 Mon --FLdgM0GNpXVMn74ppCGw 16 2012-10-23 2012 10 Tue --FnvijzY20d1nk9H7fk9w 9 2019-09-19 2019 9 Thu --GM_ORV2cYS-h38DSaCLw 38 2011-09-11 2011 9 Sun --I7YYLada0tSLkORTHb5Q 116 2014-11-07 2014 11 Fri --KCl2FvVQpvjzmZSPyviA 107 2011-07-29 2011 7 Fri --KQsXc-clkO7oHRqGzSzg 778 2010-05-02 2010 5 Sun --Ni3oJ4VOqfOEu7Sj2Vzg 1 2019-06-07 2019 6 Fri --Rsj71PBe31h5YljVseKA 309 2011-12-15 2011 12 Thu --S62v0QgkqQaVUhFnNHrw 68 2010-12-25 2010 12 Sat --SrzpvFLwP_YFwB_Cetow 150 2011-02-10 2011 2 Thu --TcDRzRIxhvHM4DSgEuMA 9 2012-03-05 2012 3 Mon --U98MNlDym2cLn36BBPgQ 3 2011-10-05 2011 10 Wed --WsruI0IGEoeRmkErU5Gg 2 2018-08-04 2018 8 Sat --Y1Adl1YUWfYIRSd8vkmA 4 2011-05-03 2011 5 Tue --Y7NhBKzLTbNliMUX_wfg 4 2015-03-26 2015 3 Thu --YPwqIlRJrhHkJcjY3eiA 2 2016-06-18 2016 6 Sat --ab39IjZR_xUf81WyTyHg 69 2010-11-23 2010 11 Tue --cZ6Hhc9F7VkKXxHMVZSQ 753 2010-04-24 2010 4 Sat --cgVkbWTiga3OYTkymKqA 3 2010-08-10 2010 8 Tue --cjBEbXMI2obtaRHNSFrA 149 2015-04-09 2015 4 Thu --e8PjCNhEz32pprnPhCwQ 1 2015-04-02 2015 4 Thu --g-a85VwrdZJNf0R95GcQ 26 2013-11-28 2013 11 Thu --i1tTcggBi4cPkd-h5hDg 93 2010-03-16 2010 3 Tue --irMpXK9y_xLlXPvPAQvw 17 2011-05-05 2011 5 Thu --kinfHwmtdjz03g8B8z8Q 3 2014-08-27 2014 8 Wed --lZAZSwpP_axKoL4lR9dQ 1 2015-09-13 2015 9 Sun --phjqoPSPa8sLmUVNby9w 48 2011-01-20 2011 1 Thu --q6datkI-f0EoVheXNEeQ 4 2014-01-28 2014 1 Tue --q7kSBRb0vWC8lSkXFByA 107 2010-09-26 2010 9 Sun --qvQS4MigHPykD2GV0-zw 1 2019-04-11 2019 4 Thu --ttCFj_csKJhxnaMRNuiw 20 2012-01-20 2012 1 Fri --ujyvoQlwVoBgMYtADiLA 285 2010-10-30 2010 10 Sat --wIGbLEhlpl_UeAIyDmZQ 2 2015-06-06 2015 6 Sat --z7PM8AGaJP0aBmGMY7RA 27 2012-09-06 2012 9 Thu -000aQFeK6tqVLndf7xORg 1 2018-10-17 2018 10 Wed -01XupAWZEXbdNbxNg5mEg 333 2010-03-23 2010 3 Tue -03HVYxkeYWaafEpNJo1SA 11 2015-11-29 2015 11 Sun -050d_XIor1NpCuWkbIVaQ 1484 2010-01-23 2010 1 Sat -05uZNVbb8DhFweTEOoDVg 23 2011-09-17 2011 9 Sat -06-Fdi30wJx-JA8P7CAng 90 2011-02-25 2011 2 Fri -092wE7j5HZOogMLAh40zA 78 2010-07-28 2010 7 Wed -0CCHBui57tZ_1y_14X-5Q 12 2017-09-23 2017 9 Sat -0CTrPQNiSyClxhdO4HSDQ 56 2010-10-13 2010 10 Wed -0DET7VdEQOJVJ_v6klEug 296 2017-05-01 2017 5 Mon -0DwB6Swi349EKfbBAOF7A 44 2011-08-03 2011 8 Wed -0FA-Qdi3SPYIoJz9UQw-A 3 2018-09-29 2018 9 Sat -0Fendn2TmhDJ-1s6gPi5g 14 2011-09-30 2011 9 Fri -0GU6ghA7z4-xotUZfXl1w 57 2011-07-20 2011 7 Wed -0Hj1hb_XW6ybWq2M7QhGA 6 2011-04-23 2011 4 Sat -0K4W5p3wbQe_vDoB5jMgQ 28 2017-08-10 2017 8 Thu -0KMvRFwDWdVBeTpT11iHw 3 2012-07-13 2012 7 Fri -0KSt9tXv6C015vmAcSIcg 23 2016-08-03 2016 8 Wed -0KqNhmK40DTzwUPM_Ik9g 144 2010-10-10 2010 10 Sun -0LPtgJC31FWMrMv317p0Q 3 2013-04-13 2013 4 Sat -0M3o2uWBnQZwd3hmfEwuw 3 2016-09-10 2016 9 Sat -0NhdsDJsdarxyDPR523ZQ 24 2010-05-10 2010 5 Mon -0NrB58jqKqJfuUCDupcsw 187 2014-06-12 2014 6 Thu -0QtTRrAMn6DKLZNef3Ojg 3 2016-07-23 2016 7 Sat -0RRiWDtfnS16AKCtfvBZg 7 2017-05-19 2017 5 Fri -0RU0vASJOV383dYA8VZgA 25 2018-04-06 2018 4 Fri -0RkJ_uIduNLWQrphbADRw 181 2018-08-30 2018 8 Thu -0Sgh0QlUKVsWosCWJzGqQ 44 2010-12-05 2010 12 Sun -0Soj75v-XoRcf2ERr8Bmg 1 2019-06-05 2019 6 Wed -0T0jfPnuBRdpNTXpOQZcA 20 2012-12-28 2012 12 Fri -0VImVWDeqewaA3th8fzIg 3 2011-01-17 2011 1 Mon -0WegMt6Cy966qlDKhu6jA 387 2013-04-04 2013 4 Thu -0XFoI1UKfuRKwyAl85zAQ 15 2012-01-08 2012 1 Sun -0YY5yQ3ufLB6EoPBsHGig 2 2012-11-01 2012 11 Thu -0ZO00Vm2ADchytlEkoXmg 60 2013-07-10 2013 7 Wed -0ZumLlFjMh4ZW1z2nXGug 5 2011-09-24 2011 9 Sat -0aIra_B6iALlfqAriBSYA 72 2015-06-27 2015 6 Sat -0a

In [0]:
display(dayofweek.select("Day of Week").distinct().head(50))

Day of Week Sun Mon Thu Sat Wed Tue Fri

In [0]:
dayofweek.write.mode("overwrite").saveAsTable("Checkin_data")